In [1]:
import sys
sys.path.append("../")

In [2]:
import torch

import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import os
import sys
import errno

from common.camera import *
from common.model import *
from common.loss import *
from common.utils import *
from common.visualization import *
from common.generators import ChunkedGenerator, UnchunkedGenerator
from time import time
from common.utils import deterministic_random

## Load and Preprocess Data

In [3]:
dataset_path = "../../data/data_3d_h36m.npz"
dataset_path_2d = '../../data/data_2d_h36m_cpn_ft_h36m_dbb.npz'

In [4]:
from common.h36m_dataset import Human36mDataset
dataset = Human36mDataset(dataset_path)

for subject in dataset.subjects():
    for action in dataset[subject].keys():
        anim = dataset[subject][action]
        
        positions_3d = []
        for cam in anim['cameras']:
            pos_3d = world_to_camera(anim['positions'], R=cam['orientation'], t=cam['translation'])
            pos_3d[:, 1:] -= pos_3d[:, :1] # Remove global offset, but keep trajectory in first position
            positions_3d.append(pos_3d)
        anim['positions_3d'] = positions_3d

In [5]:
keypoints = np.load(dataset_path_2d, allow_pickle = True)
keypoints_symmetry = keypoints['metadata'].item()['keypoints_symmetry']
kps_left, kps_right = list(keypoints_symmetry[0]), list(keypoints_symmetry[1])
joints_left, joints_right = list(dataset.skeleton().joints_left()), list(dataset.skeleton().joints_right())
keypoints = keypoints['positions_2d'].item()

for subject in dataset.subjects():
    assert subject in keypoints, 'Subject {} is missing from the 2D detections dataset'.format(subject)
    for action in dataset[subject].keys():
        assert action in keypoints[subject], 'Action {} of subject {} is missing from the 2D detections dataset'.format(action, subject)
        for cam_idx in range(len(keypoints[subject][action])):
            
            # We check for >= instead of == because some videos in H3.6M contain extra frames
            mocap_length = dataset[subject][action]['positions_3d'][cam_idx].shape[0]
            assert keypoints[subject][action][cam_idx].shape[0] >= mocap_length
            
            if keypoints[subject][action][cam_idx].shape[0] > mocap_length:
                # Shorten sequence
                keypoints[subject][action][cam_idx] = keypoints[subject][action][cam_idx][:mocap_length]

        assert len(keypoints[subject][action]) == len(dataset[subject][action]['positions_3d'])
        
for subject in keypoints.keys():
    for action in keypoints[subject]:
        for cam_idx, kps in enumerate(keypoints[subject][action]):
            # Normalize camera frame
            cam = dataset.cameras()[subject][cam_idx]
            kps[..., :2] = normalize_screen_coordinates(kps[..., :2], w=cam['res_w'], h=cam['res_h'])
            keypoints[subject][action][cam_idx] = kps

### generate subsets

In [6]:
subjects_train = ['S1', 'S5', 'S6', 'S7', 'S8']
subjects_semi = ['S7', 'S8']
subjects_test = ['S9', 'S11']

In [7]:
cameras_valid, poses_valid, poses_valid_2d = fetch(dataset = dataset,
                                                   keypoints = keypoints, 
                                                   subjects = subjects_test, 
                                                   stride = 1)

cameras_train, poses_train, poses_train_2d = fetch(dataset = dataset,
                                                   keypoints = keypoints, 
                                                   subjects = subjects_train, 
                                                   stride = 1)

cameras_semi, _, poses_semi_2d = fetch(dataset = dataset,
                                       keypoints = keypoints,
                                       subjects = subjects_semi,
                                       stride = 1)

### Define Model

In [8]:
filter_widths = [3,3,3,3,3]

In [9]:
model_pos_train = TemporalModelOptimized1f(poses_valid_2d[0].shape[-2],
                                           poses_valid_2d[0].shape[-1],
                                           poses_valid[0].shape[-2],
                                           filter_widths=filter_widths,
                                           causal =False,
                                           dropout = 0.25,
                                           channels = 1024)

In [10]:
model_traj_train = TemporalModelOptimized1f(poses_valid_2d[0].shape[-2],
                                            poses_valid_2d[0].shape[-1],
                                            1,
                                            filter_widths=filter_widths,
                                            causal =False,
                                            dropout = 0.25,
                                            channels = 1024)

In [11]:
model_pos = TemporalModel(poses_valid_2d[0].shape[-2],
                          poses_valid_2d[0].shape[-1],
                          poses_valid[0].shape[-2],
                          filter_widths=filter_widths,
                          causal =False,
                          dropout = 0.25,
                          channels = 1024,
                          dense = False)

In [12]:
model_traj = TemporalModel(poses_valid_2d[0].shape[-2],
                           poses_valid_2d[0].shape[-1],
                           1,
                           filter_widths=filter_widths,
                           causal =False,
                           dropout = 0.25,
                           channels = 1024,
                           dense = False)

In [13]:
receptive_field = model_pos.receptive_field()

In [14]:
pad = (receptive_field - 1) // 2

In [15]:
if torch.cuda.is_available():
    model_pos = model_pos.cuda()
    model_pos_train = model_pos_train.cuda()
    model_traj = model_traj.cuda()
    model_traj_train = model_traj_train.cuda()

load pretrained model

In [16]:
# checkpoint = torch.load("../../checkpoint/pretrained_h36m_cpn.bin", map_location=lambda storage, loc: storage)
# print('This model was trained for {} epochs'.format(checkpoint['epoch']))
# model_pos_train.load_state_dict(checkpoint['model_pos'])
# model_pos.load_state_dict(checkpoint['model_pos'])

form generator

In [17]:
test_generator = UnchunkedGenerator(cameras_valid, 
                                    poses_valid, 
                                    poses_valid_2d,
                                    pad=pad, 
                                    causal_shift=0, 
                                    augment=False)

In [18]:
train_generator = ChunkedGenerator(1024, 
                                   cameras_train, 
                                   poses_train, 
                                   poses_train_2d, 
                                   1,
                                   pad=pad, 
                                   causal_shift=0, 
                                   shuffle=True, 
                                   augment=False)

In [19]:
train_generator_eval = UnchunkedGenerator(cameras_train, 
                                          poses_train, 
                                          poses_train_2d,
                                          pad=pad,
                                          causal_shift=0, 
                                          augment=False)

In [20]:
semi_generator = ChunkedGenerator(1024,
                                  cameras_semi,
                                  None,
                                  poses_semi_2d,
                                  1,
                                  pad=pad,
                                  causal_shift=0,
                                  shuffle=True,
                                  random_seed=4321,
                                  augment=False,
                                  endless=True)

In [21]:
semi_generator_eval = UnchunkedGenerator(cameras_semi,
                                         None,
                                         poses_semi_2d,
                                         pad=pad,
                                         causal_shift=0,
                                         augment=False)

optimizer

In [22]:
lr = 0.001
optimizer = optim.Adam(list(model_pos_train.parameters()) + list(model_traj_train.parameters()),
                               lr=lr, amsgrad=True)

losses

In [23]:
losses_2d_train_unlabeled = []
losses_2d_train_labeled_eval = []
losses_2d_train_unlabeled_eval = []
losses_2d_valid = []

losses_traj_train = []
losses_traj_train_eval = []
losses_traj_valid = []

losses_3d_train = []
losses_3d_train_eval = []
losses_3d_valid = []

In [24]:
lr_decay = 0.95

In [25]:
epoch = 0
initial_momentum = 0.1
final_momentum = 0.001

training

In [ ]:
while epoch < 10:
    start_time = time()
    epoch_loss_3d_train = 0
    epoch_loss_traj_train = 0
    epoch_loss_2d_train_unlabeled = 0
    N = 0
    N_semi = 0
    
    # Semi-supervised scenario
    model_traj_train.train()
    model_pos_train.train()
    
    for (_, batch_3d, batch_2d), (cam_semi, _, batch_2d_semi) in zip(train_generator.next_epoch(), semi_generator.next_epoch()):
        skip = epoch < 5
        
        print(" epoch -- ", N)
        cam_semi = torch.from_numpy(cam_semi.astype('float32'))
        inputs_3d = torch.from_numpy(batch_3d.astype('float32'))
        
        if torch.cuda.is_available():
            cam_semi = cam_semi.cuda()
            inputs_3d = inputs_3d.cuda()
            
        inputs_traj = inputs_3d[:, :, :1].clone()
        inputs_3d[:, :, 0] = 0
        
        # Split point between labeled and unlabeled samples in the batch
        split_idx = inputs_3d.shape[0]

        inputs_2d = torch.from_numpy(batch_2d.astype('float32'))
        inputs_2d_semi = torch.from_numpy(batch_2d_semi.astype('float32'))
        if torch.cuda.is_available():
            inputs_2d = inputs_2d.cuda()
            inputs_2d_semi = inputs_2d_semi.cuda()
        inputs_2d_cat =  torch.cat((inputs_2d, inputs_2d_semi), dim=0) if not skip else inputs_2d

        optimizer.zero_grad()
        
        # Compute 3D poses
        predicted_3d_pos_cat = model_pos_train(inputs_2d_cat)

        loss_3d_pos = mpjpe(predicted_3d_pos_cat[:split_idx], inputs_3d)
        epoch_loss_3d_train += inputs_3d.shape[0]*inputs_3d.shape[1] * loss_3d_pos.item()
        N += inputs_3d.shape[0]*inputs_3d.shape[1]
        loss_total = loss_3d_pos
        print("loss_3d_pos : ", loss_3d_pos)
        
        
        
        # Compute global trajectory
        predicted_traj_cat = model_traj_train(inputs_2d_cat)
        w = 1 / inputs_traj[:, :, :, 2] # Weight inversely proportional to depth
        loss_traj = weighted_mpjpe(predicted_traj_cat[:split_idx], inputs_traj, w)
        epoch_loss_traj_train += inputs_3d.shape[0]*inputs_3d.shape[1] * loss_traj.item()
        assert inputs_traj.shape[0]*inputs_traj.shape[1] == inputs_3d.shape[0]*inputs_3d.shape[1]
        loss_total += loss_traj
        
        print("loss_traj : ", loss_3d_pos)
        
        if not skip:
            # Semi-supervised loss for unlabeled samples
            predicted_semi = predicted_3d_pos_cat[split_idx:]
            if pad > 0:
                target_semi = inputs_2d_semi[:, pad:-pad, :, :2].contiguous()
            else:
                target_semi = inputs_2d_semi[:, :, :, :2].contiguous()

            projection_func = project_to_2d
            reconstruction_semi = projection_func(predicted_semi + predicted_traj_cat[split_idx:], cam_semi)

            loss_reconstruction = mpjpe(reconstruction_semi, target_semi) # On 2D poses
            epoch_loss_2d_train_unlabeled += predicted_semi.shape[0]*predicted_semi.shape[1] * loss_reconstruction.item()
            if not args.no_proj:
                loss_total += loss_reconstruction
        
            N_semi += predicted_semi.shape[0]*predicted_semi.shape[1]
        else:
            N_semi += 1 # To avoid division by zero

        loss_total.backward()

        optimizer.step()
    print("loss_traj_train : ", epoch_loss_traj_train / N)
    print("loss_2d_train_unlabeled : ", epoch_loss_2d_train_unlabeled / N)
    print("loss_3d_train : ", epoch_loss_3d_train / N)
    
    losses_traj_train.append(epoch_loss_traj_train / N)
    losses_2d_train_unlabeled.append(epoch_loss_2d_train_unlabeled / N_semi)
    losses_3d_train.append(epoch_loss_3d_train / N)

 epoch --  0
loss_3d_pos :  tensor(1.2037, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(2.3512, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1024
loss_3d_pos :  tensor(1.4967, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(2.6828, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  2048
loss_3d_pos :  tensor(0.9855, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(1.7671, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  3072
loss_3d_pos :  tensor(0.8589, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(1.5188, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  4096
loss_3d_pos :  tensor(0.8083, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(1.1535, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  5120
loss_3d_pos :  tensor(0.6988, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.9826, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  6144
loss_3d_pos :  tensor(0.6112, device='cuda:0'

loss_3d_pos :  tensor(0.2999, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.3763, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  54272
loss_3d_pos :  tensor(0.3097, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.3864, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  55296
loss_3d_pos :  tensor(0.2948, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.3700, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  56320
loss_3d_pos :  tensor(0.3014, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.3817, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  57344
loss_3d_pos :  tensor(0.2927, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.3688, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  58368
loss_3d_pos :  tensor(0.2908, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.3753, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  59392
loss_3d_pos :  tensor(0.2883, device='cuda:0', grad_

loss_3d_pos :  tensor(0.2340, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2928, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  107520
loss_3d_pos :  tensor(0.2156, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2799, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  108544
loss_3d_pos :  tensor(0.2226, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2824, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  109568
loss_3d_pos :  tensor(0.2232, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2866, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  110592
loss_3d_pos :  tensor(0.2223, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2801, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  111616
loss_3d_pos :  tensor(0.2232, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2850, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  112640
loss_3d_pos :  tensor(0.2212, device='cuda:0',

loss_3d_pos :  tensor(0.1807, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2363, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  160768
loss_3d_pos :  tensor(0.1751, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2251, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  161792
loss_3d_pos :  tensor(0.1798, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2290, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  162816
loss_3d_pos :  tensor(0.1718, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2203, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  163840
loss_3d_pos :  tensor(0.1754, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2252, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  164864
loss_3d_pos :  tensor(0.1713, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2192, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  165888
loss_3d_pos :  tensor(0.1715, device='cuda:0',

loss_3d_pos :  tensor(0.1534, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.1991, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  214016
loss_3d_pos :  tensor(0.1523, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2009, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  215040
loss_3d_pos :  tensor(0.1497, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.2051, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  216064
loss_3d_pos :  tensor(0.1464, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.1950, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  217088
loss_3d_pos :  tensor(0.1495, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.1968, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  218112
loss_3d_pos :  tensor(0.1475, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.1907, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  219136
loss_3d_pos :  tensor(0.1477, device='cuda:0',

...

loss_3d_pos :  tensor(0.0244, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0310, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1347584
loss_3d_pos :  tensor(0.0261, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0386, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1348608
loss_3d_pos :  tensor(0.0243, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0316, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1349632
loss_3d_pos :  tensor(0.0250, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0322, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1350656
loss_3d_pos :  tensor(0.0246, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0321, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1351680
loss_3d_pos :  tensor(0.0252, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0350, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1352704
loss_3d_pos :  tensor(0.0242, device='cu

loss_3d_pos :  tensor(0.0245, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0320, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1400832
loss_3d_pos :  tensor(0.0246, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0328, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1401856
loss_3d_pos :  tensor(0.0241, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0330, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1402880
loss_3d_pos :  tensor(0.0242, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0318, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1403904
loss_3d_pos :  tensor(0.0241, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0321, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1404928
loss_3d_pos :  tensor(0.0249, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0344, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1405952
loss_3d_pos :  tensor(0.0241, device='cu

loss_3d_pos :  tensor(0.0248, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0316, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1454080
loss_3d_pos :  tensor(0.0239, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0322, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1455104
loss_3d_pos :  tensor(0.0246, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0359, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1456128
loss_3d_pos :  tensor(0.0247, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0331, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1457152
loss_3d_pos :  tensor(0.0245, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0312, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1458176
loss_3d_pos :  tensor(0.0255, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0347, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1459200
loss_3d_pos :  tensor(0.0240, device='cu

loss_3d_pos :  tensor(0.0249, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0331, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1507328
loss_3d_pos :  tensor(0.0244, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0332, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1508352
loss_3d_pos :  tensor(0.0255, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0360, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1509376
loss_3d_pos :  tensor(0.0250, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0338, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1510400
loss_3d_pos :  tensor(0.0259, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0325, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1511424
loss_3d_pos :  tensor(0.0247, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0331, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1512448
loss_3d_pos :  tensor(0.0248, device='cu

loss_3d_pos :  tensor(0.0271, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0375, device='cuda:0', grad_fn=<AddBackward0>)
loss_traj_train :  0.008853484178280795
loss_2d_train_unlabeled :  0.0
loss_3d_train :  0.024641369921074237
 epoch --  0
loss_3d_pos :  tensor(0.0241, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0340, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  1024
loss_3d_pos :  tensor(0.0238, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0402, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  2048
loss_3d_pos :  tensor(0.0253, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0414, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  3072
loss_3d_pos :  tensor(0.0247, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0354, device='cuda:0', grad_fn=<AddBackward0>)
 epoch --  4096
loss_3d_pos :  tensor(0.0248, device='cuda:0', grad_fn=<MeanBackward0>)
loss_traj :  tensor(0.0363, device='c